In [1]:
import polars as pl
import geopandas as gpd
import pandas as pd
import folium

In [2]:
country_codes_df = pl.read_csv('data/country_codes.csv')
df_uchazeci = pl.read_csv("data/prf_uchazeci.csv").join(other=country_codes_df, left_on="STAT_OBCANSTVI", right_on="country_name", how="left")
df_cz_uchazeci = df_uchazeci.filter(pl.col("ISO3166-1-Alpha-3") == "CZE")
df_cz_uchazeci.shape

(4441, 31)

odfiltruji uchazeče s nevyplněnou obcí

In [3]:
tmp_df = df_cz_uchazeci.filter(pl.col("OBEC_BYDLISTE") == "nevyplněno")
print(f"{tmp_df.shape[0]} uchazečů nemá vyplněné bydliště.")
del tmp_df
df_cz_uchazeci = df_cz_uchazeci.filter(pl.col("OBEC_BYDLISTE") != "nevyplněno")
print(f"{df_cz_uchazeci.shape[0]} uchazečů má vyplněné bydliště.")

2529 uchazečů nemá vyplněné bydliště.
1912 uchazečů má vyplněné bydliště.


In [4]:
places_df = pl.read_csv("data/places.csv")
# df = df.join(other=places_df, how="left", right_on="obec_name", left_on="OBEC_BYDLISTE")
df_cz_uchazeci = df_cz_uchazeci.join(other=places_df, how="left", right_on="obec_name", left_on="OBEC_BYDLISTE")
df_cz_uchazeci

shape: (2_263, 38)
┌────────────┬─────────┬─────────────┬──────────┬───┬──────────┬────────────┬─────────┬────────────┐
│ FAKULTA_SP ┆ ROK_NAR ┆ STAT_OBCANS ┆ PSC_BYDL ┆ … ┆ okres_id ┆ okres_name ┆ kraj_id ┆ kraj_name  │
│ ---        ┆ ---     ┆ TVI         ┆ ---      ┆   ┆ ---      ┆ ---        ┆ ---     ┆ ---        │
│ str        ┆ i64     ┆ ---         ┆ i64      ┆   ┆ i64      ┆ str        ┆ i64     ┆ str        │
│            ┆         ┆ str         ┆          ┆   ┆          ┆            ┆         ┆            │
╞════════════╪═════════╪═════════════╪══════════╪═══╪══════════╪════════════╪═════════╪════════════╡
│ PRF        ┆ 1998    ┆ Česká       ┆ 41705    ┆ … ┆ 3202     ┆ Beroun     ┆ 27      ┆ Středočesk │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ ý kraj     │
│ PRF        ┆ 1998    ┆ Česká       ┆ 41705    ┆ … ┆ 3307     ┆ Strakonice ┆ 35      ┆ Jihočeský  │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ kraj       │
│ PRF        ┆ 1998    ┆ Česká       ┆ 41705    ┆ … ┆ 3408     ┆ Rokycany   ┆ 43      ┆ Plzeňský   │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ kraj       │
│ PRF        ┆ 1998    ┆ Česká       ┆ 41705    ┆ … ┆ 3509     ┆ Teplice    ┆ 60      ┆ Ústecký    │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ kraj       │
│ …          ┆ …       ┆ …           ┆ …        ┆ … ┆ …        ┆ …          ┆ …       ┆ …          │
│ PRF        ┆ 1997    ┆ Česká       ┆ 41201    ┆ … ┆ 3506     ┆ Litoměřice ┆ 60      ┆ Ústecký    │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ kraj       │
│ PRF        ┆ 1997    ┆ Česká       ┆ 43921    ┆ … ┆ 3507     ┆ Louny      ┆ 60      ┆ Ústecký    │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ kraj       │
│ PRF        ┆ 1994    ┆ Česká       ┆ 41501    ┆ … ┆ 3509     ┆ Teplice    ┆ 60      ┆ Ústecký    │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆            ┆         ┆ kraj       │
│ PRF        ┆ 1997    ┆ Česká       ┆ 40011    ┆ … ┆ 3510     ┆ Ústí nad   ┆ 60      ┆ Ústecký    │
│            ┆         ┆ republika   ┆          ┆   ┆          ┆ Labem      ┆         ┆ kraj       │
└────────────┴─────────┴─────────────┴──────────┴───┴──────────┴────────────┴─────────┴────────────┘

In [5]:

gdf_obce = gpd.read_file("./vendor/obce-transformed.geojson")
# NOTE: see transform_geojsons.ipynb for where this comes from
# NOTE: PSC has 0s
# df = pl.read_csv("data/prf_uchazeci.csv").filter(pl.col("OBEC_BYDLISTE") != "nevyplněno", pl.col("OBEC_BYDLISTE") != "Osek")


In [6]:
grouped = df_cz_uchazeci.group_by("obec_id").agg(
    pl.col("OBEC_BYDLISTE").unique().alias("obce"),
    pl.col("OBEC_BYDLISTE").n_unique().alias("#obci"),
    pl.col("OBEC_BYDLISTE").sample().first().alias("obec"),
    pl.col("PSC_BYDL").sample().first().alias("PSC_BYDL"),
    pl.count("obec_id").alias("count")
)
grouped = grouped.with_columns((pl.col("obce").list.unique().count() == pl.lit(1)).alias("valid"))

assert grouped.filter(pl.col("valid").not_()).__len__() == 0
grouped

AttributeError: 'ExprListNameSpace' object has no attribute 'n_unique'

In [ ]:
m = folium.Map(tiles='cartodbpositron', location=[50.073658, 14.418540], zoom_start=8)

not_found_count = 0
for row in grouped.iter_rows(named=True):
    print(row)
    obec = row.get("obec_id")
    count = row["count"]
    # print(gdf_obce.columns)
    selected_feature = gdf_obce[gdf_obce['id'] == str(obec)]
    if selected_feature is None or len(selected_feature) == 0:
        not_found_count += 1
        print(f"Not found: {obec}")
        continue
    folium.GeoJson(selected_feature).add_to(m)
    # folium.GeoJson(selected_feature).add_to(m)
    # label_value = row[1]

    # if len(selected_feature['geometry'].centroid.y.values) == 0:
    #     continue
    # if len(selected_feature['geometry'].centroid.x.values) == 0:
    #     continue

    folium.Marker(
        location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
        icon=folium.DivIcon(html=f'<div style="font-size: 9pt; color: black; font-family: monospace;">{count}</div>')
    ).add_to(m)
not_found_count

{'obec_id': 567337, 'obce': ['Obrnice'], '#obci': 1, 'obec': 'Obrnice', 'PSC_BYDL': 43401, 'count': 1, 'valid': True}
{'obec_id': 564044, 'obce': ['Hejnice'], '#obci': 1, 'obec': 'Hejnice', 'PSC_BYDL': 46362, 'count': 1, 'valid': True}
{'obec_id': 582786, 'obce': ['Brno'], '#obci': 1, 'obec': 'Brno', 'PSC_BYDL': 62500, 'count': 9, 'valid': True}
{'obec_id': 554481, 'obce': ['Cheb'], '#obci': 1, 'obec': 'Cheb', 'PSC_BYDL': 35002, 'count': 7, 'valid': True}


/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].

{'obec_id': 538094, 'obce': ['Brandýs nad Labem-Stará Boleslav'], '#obci': 1, 'obec': 'Brandýs nad Labem-Stará Boleslav', 'PSC_BYDL': 25001, 'count': 7, 'valid': True}
{'obec_id': 565628, 'obce': ['Vinařice'], '#obci': 1, 'obec': 'Vinařice', 'PSC_BYDL': 43915, 'count': 2, 'valid': True}
{'obec_id': 565741, 'obce': ['Travčice'], '#obci': 1, 'obec': 'Travčice', 'PSC_BYDL': 41201, 'count': 2, 'valid': True}
{'obec_id': 550027, 'obce': ['Záhoří'], '#obci': 1, 'obec': 'Záhoří', 'PSC_BYDL': 51301, 'count': 1, 'valid': True}
{'obec_id': 565229, 'obce': ['Lovosice'], '#obci': 1, 'obec': 'Lovosice', 'PSC_BYDL': 41002, 'count': 17, 'valid': True}
{'obec_id': 566152, 'obce': ['Domoušice'], '#obci': 1, 'obec': 'Domoušice', 'PSC_BYDL': 43968, 'count': 1, 'valid': True}
{'obec_id': 559733, 'obce': ['Březina'], '#obci': 1, 'obec': 'Březina', 'PSC_BYDL': 33824, 'count': 1, 'valid': True}
{'obec_id': 555398, 'obce': ['Nová Role'], '#obci': 1, 'obec': 'Nová Role', 'PSC_BYDL': 36225, 'count': 1, 'valid':

/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].

{'obec_id': 563404, 'obce': ['Vejprty'], '#obci': 1, 'obec': 'Vejprty', 'PSC_BYDL': 43191, 'count': 1, 'valid': True}
{'obec_id': 547794, 'obce': ['Hodonín'], '#obci': 1, 'obec': 'Hodonín', 'PSC_BYDL': 69501, 'count': 2, 'valid': True}
{'obec_id': 570877, 'obce': ['Smiřice'], '#obci': 1, 'obec': 'Smiřice', 'PSC_BYDL': 50303, 'count': 1, 'valid': True}
{'obec_id': 562335, 'obce': ['Děčín'], '#obci': 1, 'obec': 'Děčín', 'PSC_BYDL': 40502, 'count': 118, 'valid': True}
{'obec_id': 564711, 'obce': ['Čížkovice'], '#obci': 1, 'obec': 'Čížkovice', 'PSC_BYDL': 41112, 'count': 3, 'valid': True}
{'obec_id': 534676, 'obce': ['Mělník'], '#obci': 1, 'obec': 'Mělník', 'PSC_BYDL': 27601, 'count': 5, 'valid': True}
{'obec_id': 534161, 'obce': ['Křesetice'], '#obci': 1, 'obec': 'Křesetice', 'PSC_BYDL': 28401, 'count': 1, 'valid': True}
{'obec_id': 566551, 'obce': ['Peruc'], '#obci': 1, 'obec': 'Peruc', 'PSC_BYDL': 44001, 'count': 1, 'valid': True}
{'obec_id': 554499, 'obce': ['Aš'], '#obci': 1, 'obec': 

...

{'obec_id': 565083, 'obce': ['Křešice'], '#obci': 1, 'obec': 'Křešice', 'PSC_BYDL': 41148, 'count': 8, 'valid': True}
{'obec_id': 530204, 'obce': ['Mrač'], '#obci': 1, 'obec': 'Mrač', 'PSC_BYDL': 25721, 'count': 2, 'valid': True}
{'obec_id': 563889, 'obce': ['Liberec'], '#obci': 1, 'obec': 'Liberec', 'PSC_BYDL': 46006, 'count': 4, 'valid': True}
{'obec_id': 555380, 'obce': ['Nejdek'], '#obci': 1, 'obec': 'Nejdek', 'PSC_BYDL': 36221, 'count': 1, 'valid': True}
{'obec_id': 588270, 'obce': ['Žatec'], '#obci': 1, 'obec': 'Žatec', 'PSC_BYDL': 43801, 'count': 6, 'valid': True}
{'obec_id': 566128, 'obce': ['Deštnice'], '#obci': 1, 'obec': 'Deštnice', 'PSC_BYDL': 43801, 'count': 1, 'valid': True}
{'obec_id': 565211, 'obce': ['Lovečkovice'], '#obci': 1, 'obec': 'Lovečkovice', 'PSC_BYDL': 41145, 'count': 2, 'valid': True}
{'obec_id': 532053, 'obce': ['Kladno'], '#obci': 1, 'obec': 'Kladno', 'PSC_BYDL': 27203, 'count': 9, 'valid': True}
{'obec_id': 581976, 'obce': ['Lomnice'], '#obci': 1, 'obec':

/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].

{'obec_id': 581330, 'obce': ['Benešov'], '#obci': 1, 'obec': 'Benešov', 'PSC_BYDL': 25601, 'count': 3, 'valid': True}
{'obec_id': 567167, 'obce': ['Hora Svaté Kateřiny'], '#obci': 1, 'obec': 'Hora Svaté Kateřiny', 'PSC_BYDL': 43546, 'count': 1, 'valid': True}
{'obec_id': 502545, 'obce': ['Horka nad Moravou'], '#obci': 1, 'obec': 'Horka nad Moravou', 'PSC_BYDL': 78335, 'count': 1, 'valid': True}
{'obec_id': 546186, 'obce': ['Ryjice'], '#obci': 1, 'obec': 'Ryjice', 'PSC_BYDL': 40331, 'count': 2, 'valid': True}
{'obec_id': 537683, 'obce': ['Poděbrady'], '#obci': 1, 'obec': 'Poděbrady', 'PSC_BYDL': 29001, 'count': 4, 'valid': True}
{'obec_id': 537799, 'obce': ['Senice'], '#obci': 1, 'obec': 'Senice', 'PSC_BYDL': 29001, 'count': 1, 'valid': True}
{'obec_id': 565857, 'obce': ['Velké Žernoseky'], '#obci': 1, 'obec': 'Velké Žernoseky', 'PSC_BYDL': 41201, 'count': 1, 'valid': True}
{'obec_id': 585513, 'obce': ['Napajedla'], '#obci': 1, 'obec': 'Napajedla', 'PSC_BYDL': 76361, 'count': 1, 'valid'

/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].centroid.x.values[0]],
/tmp/ipykernel_1898590/1311140762.py:24: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[selected_feature['geometry'].centroid.y.values[0], selected_feature['geometry'].

0

In [ ]:
m

In [ ]:
# saving to file
import io
from PIL import Image

img_data = m._to_png(5)
img = Image.open(io.BytesIO(img_data))
img.save('mesta.png')